In [1]:
%pylab inline
import pandas as pd
import json
import difflib
import time
start=time.time()
pd.options.display.max_rows = 2000

from mtranslate import translate

from IPython.core.display import HTML

Populating the interactive namespace from numpy and matplotlib


In [2]:
HTML('''<script>
code_show=true;
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
}
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit"
value="Click here to toggle on/off the raw code."></form>''')

A furcsa ékezetű betüket konvertálja.

In [4]:
def convert_c2(string):
    if(isinstance(string, str)):
        for c in ["ş","š"]:
            if(c in string): 
                string=string.replace(c,"ș")
        for c in ["ţ"]:
            if(c in string): 
                string=string.replace(c,"ț")
        for c in ["ã"]:
            if(c in string): 
                string=string.replace(c,"ă")
        for c in ["à"]:
            if(c in string): 
                string=string.replace(c,"á")
        for c in ["è","ė"]:
            if(c in string): 
                string=string.replace(c,"é")
        for c in ["ì"]:
            if(c in string): 
                string=string.replace(c,"í")
        for c in ["ò"]:
            if(c in string): 
                string=string.replace(c,"ó")      
        for c in ["ô"]:
            if(c in string): 
                string=string.replace(c,"ő")
        for c in ["ù"]:
            if(c in string): 
                string=string.replace(c,"ú")  
        for c in ["\"","\'","*","!",".","?",":","(",")",'”','„','•','…','ℓ','ℳ','←','→','│','║','▂','▃','▄','▅','▆','▇','█','▌','♥','♫','✂','✌','✖''|','£','©',"^","$","--"]:
            if(c in string): 
                string=string.replace(c,"")
        for c in [" \\ "," \\","\\ ","\\"," / "," /","/ ","/"]:
            if(c in string): 
                string=string.replace(c,", ")
        for c in [" - "," -","- "]:
            if(c in string): 
                string=string.replace(c,"-")
        return string

In [5]:
tprev=""
tprev_t=""
sprev=""
special1=["a","e","i","o","u","s","t"," ","-"]
special2=["ö","ü","ó","ő","ú","ű","é","á","í","ă","î","â","ș","ț"," ","-"]
a=[]
b=[]

Dataframe-et lefordító függvény.

In [6]:
def translate_s1(string):
    #print(string,"->")
    global tprev
    global tprev_t
    if isinstance(string, str):
        if(string != tprev):
            tprev=string
            trans=translate(string,to_language='en')
            tprev_t=trans
        string=tprev_t
    #print(string)
    return string

In [67]:
def translate_s2(string):
    #print(string,"->")
    global tprev
    global tprev_t
    if isinstance(string, str):
        if(string != tprev):
            tprev=string
            trans=translate(string,'en',from_language="hu")
            if(trans == string):
                trans=translate(string,'en',from_language="ro")
                if(trans == string):
                    trans=translate(string,'en',from_language="de")
            tprev_t=trans
        string=tprev_t
    #print(string)
    return string

Betük sorrendjét nem veszi figyelembe...

In [68]:
def convert_s(string):
    #print(data[data["id"]==34]["workwhat"])
    #print(string,"->")
    num=0
    prev_special=False
    global sprev
    if isinstance(string, str) :
        enumerate(difflib.ndiff(sprev, string))
        for i,s in enumerate(difflib.ndiff(sprev, string)):
            print(s)
            if s[2] in special:
                if s[0]=='-':
                    num+=1
                    prev_special=True
                elif s[0]=="+" :
                    if prev_special:
                        num-=1
                        prev_special=False
                    else:
                        num+=1
                        prev_special=True
            elif s[0]=='+' or s[0]=='-': 
                num+=1
            print(num)
        #if abs(num)<2 and len(sprev)-len(string)<2: 
            #return sprev
    #print(num)
    #return string

A hiányzo betuk szama es a hossz kapcsolatban kell legyenek

In [69]:
def convert_s2(string):
    #print(data[data["id"]==34]["workwhat"])
    #print(string,"->")
    num=0
    nums=0
    chars=zeros(513)    
    global sprev
    if isinstance(string, str) :
        for i,s in enumerate(difflib.ndiff(sprev, string)):
            #print(s)
            if(ord(s[2])<512):
                if s[2] in special2 and s[0]=='-': nums+=1
                elif s[2] in special1 and s[0]=='+': nums-=1
                else:
                    if s[0]=='+': chars[ord(s[2])]+=1
                    elif s[0]=='-': chars[ord(s[2])]-=1
                #print(abs(nums),"  ",sum(abs(chars)),len(string)-len(sprev))
            else: return string
        if(abs(abs(nums)+sum(abs(chars))-abs(len(string)-len(sprev)))<2 and len(string)-len(sprev)<2): return sprev
        else:
            sprev=string
            return string

In [7]:
data=pd.DataFrame.from_dict(json.loads(open("data.json").read()))

In [93]:
for i in [14,15,17,18]:
    x=data.groupby(data.columns[i])
    y=x.count()
    a.append(size(y.index))

Előszőr mindent kicsi betüre váltok (13ik oszloptól kezdve), utána a rossz karakterektől megszabadulok. Ezt követően a nem elérhető adatokat kiszűröm. A harmadik lépés a kevés karakterben különböző szavak összevonása (ovono -> ovónő, kell a fordítóhoz). Utolsó lépésként lefordítom a szavakat.

In [94]:
data.columns

Index(['birth', 'id', 'livesin', 'marriedsince', 'marriedto', 'name', 'other1',
       'other2', 'other3', 'other4', 'other5', 'other6', 'school',
       'schoolyear', 'studwhat', 'studwhere', 'studyear', 'workwhat',
       'workwhere'],
      dtype='object')

Kis betűk

In [95]:
for i in [12,14,15,17,18]:#studwhat studwhere studyear workwhat workwhere
    data[data.columns[i]]=data[data.columns[i]].str.lower()

Rossz karakterek mennek

In [96]:
for i in data.columns[2:]:# id-n kivul minden
    data[i]=data[i].apply(convert_c2)

NaN

In [97]:
data.replace(to_replace=["-","--","---",None,"?",""],value=NaN,inplace=True)

Az ékezet nélküli szavakat kijavítom

In [98]:
for i in [2,12,14,15,17,18]:#livesin school studwhat studwhere workwhat workwhere
    data.sort_values(by=data.columns[i],inplace=True,ascending=False)
    data[data.columns[i]]=data[data.columns[i]].apply(convert_s2)

Lefordítom

In [99]:
for i in [14,17]: #studwhat workwhat
    data.sort_values(by=data.columns[i],inplace=True,ascending=False)
    data[data.columns[i]]=data[data.columns[i]].apply(translate_s2)

Kis betűk még egyszer

In [100]:
for i in [12,14,15,17,18]:#school studwhat studwhere studyear workwhat workwhere
    data[data.columns[i]]=data[data.columns[i]].str.lower()

In [101]:
for i in [14,15,17,18]:
    x=data.groupby(data.columns[i])
    y=x.count()
    b.append(size(y.index))

1000 személy: 192 s a legujabb teljesítmény

In [102]:
x=data.groupby("livesin")
y=x.count()
y.sort_values(by="id",ascending=False)

birth    id  marriedsince  \
livesin                                                                         
Cluj-Napoca                                          5000  5000           436   
Sepsiszentgyorgy                                     2575  2575           348   
Targu-Mures                                          2442  2442           294   
Csikszereda                                          1846  1846           187   
Székelyudvarhely                                     1818  1818           256   
Kézdivásárhely, Covasna, Romania                     1679  1679           163   
Budatétény, Budapest, Hungary                        1549  1549           147   
Székelykeresztur, Harghita, Romania                  1186  1186           138   
Toplita-Ciuc, Harghita, Romania                      1123  1123            98   
Szentegyházasfalu                                    1106  1106            69   
Sighisoara, Romania                                  1069  1069            99   
Gyergyószentmiklós                                    973   973           102   
Marosvásárhely, Mures, Romania                        944   944           154   
Reghin-Sat, Mures, Romania                            941   941            99   
Parajd                                                831   831            61   
Sovata Bai, Mures, Romania                            814   814            35   
Barót, Covasna, Romania                               709   709            67   
Bucharest, Romania                                    681   681            46   
Balan, Salaj, Romania                                 557   557            48   
Brassó, Brasov, Romania                               470   470            56   
London, United Kingdom                                408   408            53   
Reghinul, Mures, Romania                              292   292            34   
Sfântul-Gheorghe, Covasna, Romania                    289   289            35   
Vlahita, Harghita, Romania                            245   245            14   
Szováta, Mures, Romania                               210   210             9   
Miercurea-Ciucului, Harghita, Romania                 194   194            24   
Gyergyóalfalu, Harghita, Romania                      170   170            19   
Rome, Italy                                           146   146            14   
Baraolt                                               134   134            10   
Csomafalva, Harghita, Romania                         118   118            14   
Timișoara, Romania                                    116   116            10   
Gyergyóremete, Harghita, Romania                      105   105            17   
Gelsenkirchen, Germany                                105   105            12   
Ditro, Harghita, Romania                              104   104            15   
Oradea-Mare, Bihor, Romania                            91    91            13   
Madrid, Spain                                          90    90             9   
Balánbánya, Harghita, Romania                          88    88             2   
Sibiu, Romania                                         87    87            14   
Vienna, Austria                                        85    85             8   
Munich, Germany                                        84    84             4   
Torja, Covasna, Romania                                77    77             5   
Nagybacon                                              77    77             6   
Gheorghieni, Harghita, Romania                         77    77             7   
Vargyas                                                73    73             8   
Kézdisznetlélek, Covasna, Romania                      71    71             8   
Kovászna, Covasna, Romania                             69    69            10   
Ozsdola                                                67    67             7   
Odorheiul Secuiesc, Harghita, Romania                  64    64             6   
Na

Mennyire sikerült tömöríteni az adatokat

In [103]:
for i in arange(len(a)):#school studwhat studwhere workwhat workwhere
    print((a[i]-b[i])/a[i]*100,"%")  

21.428571428571427 %
20.260905014268243 %
23.787625418060202 %
13.006707494896471 %
24.480628860190905 %
20.487168334058286 %
25.429628018272787 %
14.522072104616718 %


In [104]:
data.sort_values(by="id",inplace=True)

In [105]:
data.to_json("first.json")

In [109]:
data["id"]

0            0
1            1
2            2
3            3
4            4
5            5
6            6
7            7
8            8
9            9
10          10
11          11
12          12
13          13
14          14
15          15
16          16
17          17
18          18
19          19
20          20
21          21
22          22
23          23
24          24
25          25
26          26
27          27
28          28
29          29
30          30
31          31
32          32
33          33
34          34
35          35
36          36
37          37
38          38
39          39
40          40
41          41
42          42
43          43
44          44
45          45
46          46
47          47
48          48
49          49
50          50
51          51
52          52
53          53
54          54
55          55
56          56
57          57
58          58
59          59
60          60
61          61
62          62
63          63
64          64
65          65
66        

Kb 18 perc az 5000 szemely

In [54]:
all_data.to_json("first2.json")

In [91]:
data.sort_values(by='studwhere',ascending=False)

birth     id                                      livesin  \
8808       szovata   8808                   Sovata Bai, Mures, Romania   
242        vlahica    242                                         None   
16085      szovata  16085                            Bangkok, Thailand   
910        szovata    910                   Sovata Bai, Mures, Romania   
11495    kolozsvar  11495                                  Cluj-Napoca   
13976      toplita  13976              Toplita-Ciuc, Harghita, Romania   
16426  szentgyorgy  16426                       London, United Kingdom   
18474        regen  18474                                         None   
10238      toplita  10238                     Reghinul, Mures, Romania   
14673      toplita  14673              Toplita-Ciuc, Harghita, Romania   
9180       toplita   9180              Toplita-Ciuc, Harghita, Romania   
19042        regen  19042                   Reghin-Sat, Mures, Romania   
661          regen    661                   Reghin-Sat, Mures, Romania   
3463         regen   3463                   Reghin-Sat, Mures, Romania   
11937        regen  11937                     Reghinul, Mures, Romania   
19324        regen  19324                     Reghinul, Mures, Romania   
18501        regen  18501                   Reghin-Sat, Mures, Romania   
6214         regen   6214                   Reghin-Sat, Mures, Romania   
14907      szovata  14907                   Sovata Bai, Mures, Romania   
705    csikszereda    705                Szilágysomlyó, Salaj, Romania   
8399       gyergyo   8399             Gyergyóalfalu, Harghita, Romania   
12945  szentgyorgy  12945                Budatétény, Budapest, Hungary   
11356  szentgyorgy  11356                             Sepsiszentgyorgy   
2501         barot   2501                                   Alsónémedi   
8574       vlahica   8574                Budatétény, Budapest, Hungary   
19671      szovata  19671                   Sovata Bai, Mures, Romania   
19343     kovaszna  19343                                         None   
2717     udvarhely   2717                                 Metz, France   
4197   csikszereda   4197                               Gyimesközéplok   
15529  csikszereda  15529                               Gyimesközéplok   
7282       gyergyo   7282            Gyimesfelsölok, Harghita, Romania   
3979        parajd   3979                                         None   
14872       parajd  14872                                       Parajd   
3088        parajd   3088                                       Parajd   
7111      kovaszna   7111                             Sepsiszentgyorgy   
1841        parajd   1841                                       Parajd   
4653   szentgyorgy   4653                                     Nagyajta   
2268   szentgyorgy   2268                                         None   
14279        kezdi  14279                    Bretcul, Covasna, Romania   
5049      kovaszna   5049                Uzonkafürdö, Covasna, Romania   
17564    keresztur  17564                             Sepsiszentgyorgy   
17784     kovaszna  17784                                          Érd   
14840  szentgyorgy  14840                                          Érd   
15869  szentgyorgy  15869                Budatétény, Budapest, Hungary   
15944      gyergyo  15944                Budatétény, Budapest, Hungary   
18152      gyergyo  18152                   Borszék, Harghita, Romania   
13235    keresztur  13235          Székelykeresztur, Harghita, Romania   
8592     keresztur   8592                                         None   
19552    keresztur  19552           Alsóbóldogfalva, Harghita, Romania   
13735    keresztur  13735                     Ditro, Harghita, Romania   
10252    keresztur  10252                    Santa Barbara, California   
17778    keresztur  17778                                         None   
11565    keresztur  11565          Székelykeresztur, Harghita, Romania   
11966    keresztu

studwhere  \
0               orbán balázs gimnázium, székelykeresztúr   
1                                                   None   
2                       northeastern illinois university   
3                                                   None   
4                                                   None   
5                           nagy istván művészeti liceum   
6                                                   None   
7                                                   None   
8                                                   None   
9                                                   None   
10                                                  None   
11                                                  None   
12                                                  None   
13                         sapientia emte marosvásárhely   
14               gábor áron szakközépiskola szentegyháza   
15     universitatea transilvania brasov facultatea d...   
16                                                  None   
17                                                  None   
18                egeszsegugyi foiskola szekelyudvarhely   
19                    akg bp, sapientia emte csíkszereda   
20                                                  None   
21                                                  None   
22                                                  None   
23                              egeszsegugyi posztliceum   
24     tamási áron gimnázium egészségügyi asszisztens...   
25                    egeszsegugyi technikum csikszereda   
26                                                  None   
27                                                  None   
28                 umf iuliu hatieganu cluj-napoca, cluj   
29                  bányai jános műszaki szakközépiskola   
30                                         uni wuppertal   
31          az élet iskolája amit soha nem lehet kijárni   
32     tessedik sámuel főiskola pedagógiai főiskolai ...   
33                                                  None   
34                                                  None   
35             nagy mózes elméleti líceum-kézdivásárhely   
36                               babeș-bolyai university   
37                                                  None   
38                                                  None   
39                     umf targu mures, medicina dentara   
40                                                  None   
41         academia de muzică gheorghe dima, cluj-napoca   
42                       babes-bolyai university of cluj   
43                               gépgyártó iskolaközpont   
44                                                  None   
45                                                  None   
46                                                  None   
47                                                  None   
48                                                  None   
49                                                  None   
50                  palló imre művészeti szakközépiskola   
51                          st helena junior high school   
52                                                  None   
53                                                  None   
54                       colegiul universitar medical bv   
55                                                  None   
56                                                  None   
57     marosvásárhely szentgyörgy istván színmüvészet...   
58                                                  None   
59                                                  None   
60                          bányai jános szakközépiskola   
61      facultatea de fizica, universitatea babes bolyai   
62                                                  None   
63                                                  None   
64                    baróti szabó dávid szakközépiskola   
65                                                  None   
66                         